In [0]:
%run ../../config/project_config

In [0]:
%run ../../src/utils

In [ ]:
from pyspark.sql import functions as F

In [0]:
df_fact = spark.table(f"{CATALOG_NAME}.{SCHEMA_SILVER}.county_metrics")

In [0]:
df_crosswalk = spark.table(f"{CATALOG_NAME}.{SCHEMA_BRONZE}.v_countycrosswalk_zillow")
df_cities = spark.table(f"{CATALOG_NAME}.{SCHEMA_BRONZE}.v_cities_crosswalk")

In [0]:
df_crosswalk = standardize_dataframe_headers(df_crosswalk)
df_cities = standardize_dataframe_headers(df_cities)

In [0]:
df_enriched = df_fact.alias("metrics").join(
    df_crosswalk.alias("cross"),
    F.col("metrics.region_name") == F.col("cross.county_name"), # Aligning keys based on available columns
    how="left"
)

In [0]:
df_enriched = df_fact.alias("metrics").join(
    df_crosswalk.alias("cross"),
    F.col("metrics.region_name").cast("int") == F.col("cross.fips"),
    how="left"
)

In [0]:
df_enriched = df_enriched.drop(F.col("cross.fips")) \
                         .drop(F.col("cross.rescued_data"))

In [0]:
df_final_enriched = df_enriched.alias("enriched").join(
    df_cities.alias("city"),
    (F.col("enriched.county_name") == F.col("city.county")) & 
    (F.col("enriched.state_name") == F.col("city.state")),
    how="left"
)

In [0]:
display(df_final_enriched)

date region_name days_on_zillow_all_homes inventory_seasonally_adjusted_all_homes inventory_raw_all_homes median_listing_price_per_sqft_1_bedroom median_listing_price_per_sqft_2_bedroom median_listing_price_per_sqft_3_bedroom median_listing_price_per_sqft_4_bedroom median_listing_price_per_sqft_5_bedroom_or_more median_listing_price_per_sqft_all_homes median_listing_price_per_sqft_condo_coop median_listing_price_per_sqft_duplex_triplex median_listing_price_per_sqft_single_family_residence median_listing_price_1_bedroom median_listing_price_2_bedroom median_listing_price_3_bedroom median_listing_price_4_bedroom median_listing_price_5_bedroom_or_more median_listing_price_all_homes median_listing_price_condo_coop median_listing_price_duplex_triplex median_listing_price_single_family_residence median_pct_of_price_reduction_all_homes median_pct_of_price_reduction_condo_coop median_pct_of_price_reduction_single_family_residence median_price_cut_dollar_all_homes median_price_cut_dollar_condo_coop median_price_cut_dollar_single_family_residence median_rental_price_per_sqft_1_bedroom median_rental_price_per_sqft_2_bedroom median_rental_price_per_sqft_3_bedroom median_rental_price_per_sqft_4_bedroom median_rental_price_per_sqft_5_bedroom_or_more median_rental_price_per_sqft_all_homes median_rental_price_per_sqft_condo_coop median_rental_price_per_sqft_duplex_triplex median_rental_price_per_sqft_multi_family_residence5_plus_units median_rental_price_per_sqft_single_family_residence median_rental_price_per_sqft_studio median_rental_price_1_bedroom median_rental_price_2_bedroom median_rental_price_3_bedroom median_rental_price_4_bedroom median_rental_price_5_bedroom_or_more median_rental_price_all_homes median_rental_price_condo_coop median_rental_price_duplex_triplex median_rental_price_multi_family_residence5_plus_units median_rental_price_single_family_residence median_rental_price_studio zhviper_sqft_all_homes pct_of_homes_decreasing_in_values_all_homes pct_of_homes_increasing_in_values_all_homes pct_of_homes_selling_for_gain_all_homes pct_of_homes_selling_for_loss_all_homes pct_of_listings_with_price_reductions_seas_adj_all_homes pct_of_listings_with_price_reductions_seas_adj_condo_coop pct_of_listings_with_price_reductions_seas_adj_single_family_residence pct_of_listings_with_price_reductions_all_homes pct_of_listings_with_price_reductions_condo_coop pct_of_listings_with_price_reductions_single_family_residence price_to_rent_ratio_all_homes sale_counts sale_counts_seas_adj sale_prices zhvi_1bedroom zhvi_2bedroom zhvi_3bedroom zhvi_4bedroom zhvi_5_bedroom_or_more zhvi_all_homes zhvi_bottom_tier zhvi_condo_coop zhvi_middle_tier zhvi_single_family_residence zhvi_top_tier zri_all_homes zri_all_homes_plus_multifamily zri_per_sqft_all_homes zri_multi_family_residence_rental zri_single_family_residence_rental county_name state_name state_fips county_fips metro_name_zillow cbsaname county_region_id_zillow metro_region_id_zillow cbsacode city 2017-06-30 54029 null null null null 68.8061938061938 69.4444444444444 null null 69.4444444444444 null null 69.4444444444444 null null 95000 null null 89900 null null 89900 null null null null null null null null null null null null null null null null null null null null null null null null null null null null 62 26.48 68.83 null null null null null null null null 8.9 null null null 50000 null 86500 94000 null 81200 53000 null 81200 81200 141300 761 758 0.624 706 760 Hancock West Virginia 54 29 Weirton, OH Weirton-Steubenville, WV-OH 1757 395217 48260 null 2017-07-31 12085 108.5 1478 1418 null 143.56011724338 182.327044025157 191.029900332226 203.445469343462 177.830112545339 126.377597109304 null 185 null 173900 370000 509900 739450 339875 159000 null 399950 2.77777777777778 3.27695416568498 2.626454023896 10000 5100 10000 null 1.25 1.20408163265306 null null 1.23050497066245 1.25167965195804 null 1.25622119815668 1.2155416244512 null null 1400 2125 null null 1800 1400 null 1389.5 2150 null 155 8.4 86.

In [0]:
df_final_enriched = df_final_enriched.drop(F.col("city.county")) \
    .drop(F.col("city.state")) \
    .drop(F.col("city.rescued_data")) \
    .drop(F.col("city.unique_city_id"))
                             

In [0]:
(df_final_enriched.write
    .format("delta")
    .mode("overwrite")
    .option("overwriteSchema", "true")
    .clusterBy("region_name", "date") 
    .saveAsTable(f"{CATALOG_NAME}.{SCHEMA_SILVER}.county_crosswalk_metrics"))